In [2]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np
import json
import requests

BAGP_URL = "https://www.bayareagreenprint.org/api/"

# Using the API

In [ ]:
# All counties in the Bay Area

bay_area_county_names = ['Marin',
 'San Mateo',
 'Napa',
 'Contra Costa',
 'Santa Clara',
 'Alameda',
 'Sonoma',
 'San Francisco',
 'Solano']

### Defining functions that extract census data to feed into the API.

In [ ]:
# Get coordinates from county name.

def get_county_coordinates(county):
    f = open("county_data.json", encoding = "ISO-8859-1")
    data = json.load(f)
    #print(data["features"][0])

    for c in data["features"]:
        if c["properties"]["NAME"] == county:
            county_coordinates = c["geometry"]['coordinates']
            county_data = c
    return county_coordinates

print(len(get_county_coordinates("San Francisco")))


6


In [ ]:
# Use API to extract ANALYSIS_AREA from a county name and it's coordinates.

def get_analysis_area(name, coordinates, poly_type):
    ANALYSIS_AREA = {
        "name": name,
        "type": "FeatureCollection",
        "crs": {
            "properties": {
                "name": "urn:ogc:def:crs:OGC:1.3:CRS84"
            },
            "type": "name"
        },
        "features": [
            {
                "type": "Feature",
                "geometry": {
                    "coordinates": coordinates,
                    "type": poly_type
                },
                "properties": {
                    "name": name,
                }
            }
        ]
    }
    return ANALYSIS_AREA

In [ ]:
# Gets country coordinates from Census Tract with input geo_id
# geo_id is an ID from the county_data dataset

def get_tract_coordinates(geo_id):
    f = open("tract.json", encoding = "ISO-8859-1")
    data = json.load(f)
    #print(data["features"][0])
    tract_coordinates = 0
    poly_type = ""
    for c in data["features"]:
        if c["properties"]["GEOID"] == geo_id:
            tract_coordinates = c["geometry"]['coordinates']
            poly_type = c["geometry"]['type']
            county_data = c
    return tract_coordinates, poly_type

In [ ]:
# Testing functions on Alameda County

cords, poly_type = get_tract_coordinates("06085507301")
area = get_analysis_area("Alameda County",cords, poly_type)
response = requests.post(BAGP_URL, json=area)
response = response.json()

response['features'][0]['properties']

{'coastalhabitatvulnerable_unit': 'acres',
 'linkage_diffuse_percent': 0,
 'carbon_urbanforest_value': 129937,
 'linkage_channelized_value': 0,
 'floodplain500_natural_warning': '',
 'grazing_percent': 0,
 'lc_coniferhardwoodmix_value': 226,
 'statefarm_percent': 0,
 'pollutioncancer_warning': '',
 'transitpriorityareas': 0,
 'tsunami_value': 0,
 'impair303stream_value': True,
 'stormwaterretentionpools_units': 'pools',
 'naturalseminaturallands_unit': 'acres',
 'linkage_large_value': 0,
 'baylands_unit': 'acres',
 'wetlands_protected_value': 0,
 'liquefaction_value': 55,
 'naturalseminaturallands_warning': '',
 'cropdollars_warning': '',
 'naturalbaylands_value': 0,
 'fishbarrier_unit': 'count',
 'clnpriority_value': 0,
 'lc_conifer_protected_unit': 'acres',
 'prinathab_marginal_warning': '',
 'floodplain100_value': 36,
 'trailmilesexist_unit': 'miles',
 'seismichazard_warning': '',
 'watersites_planned_unit': 'count',
 'groundwaterdependentecosystems_percent': 3,
 'prinathab_ok_unit'

# Getting the Census Tract Data

In [ ]:
f = open("tract.json", encoding = "ISO-8859-1")
data = json.load(f)
len(data['features'])
data['features'][0]
#print(data)

{'type': 'Feature',
 'geometry': {'bbox': [-118.263307, 33.782888, -118.253038, 33.791596],
  'type': 'Polygon',
  'coordinates': [[[-118.263307, 33.791148],
    [-118.25521000000002, 33.791596],
    [-118.25394199999998, 33.791414],
    [-118.253038, 33.791248],
    [-118.25314900000001, 33.789274],
    [-118.253713, 33.7872],
    [-118.253525, 33.784408],
    [-118.25356299999999, 33.783209],
    [-118.258121, 33.782925],
    [-118.25957399999999, 33.783055],
    [-118.26265600000002, 33.782888],
    [-118.26295700000001, 33.786701],
    [-118.263307, 33.791148]]]},
 'properties': {'STATEFP': '06',
  'COUNTYFP': '037',
  'TRACTCE': '294610',
  'AFFGEOID': '1400000US06037294610',
  'GEOID': '06037294610',
  'NAME': '2946.10',
  'NAMELSAD': 'Census Tract 2946.10',
  'STUSPS': 'CA',
  'NAMELSADCO': 'Los Angeles County',
  'STATE_NAME': 'California',
  'LSAD': 'CT',
  'ALAND': 823808,
  'AWATER': 0}}

In [ ]:
def get_all_tracts(counties):
    df = pd.DataFrame()
    BAGP_URL = "https://www.bayareagreenprint.org/api/"
    unwanted_properties = ["waterpolicies", "habitatpolicies", "intersections","conservationpolicies"]
    f = open("tract.json", encoding = "ISO-8859-1")
    data = json.load(f)
    for t in data["features"]: #i in range (500):
        #t = data["features"][i]
        if t["properties"]["NAMELSADCO"] in counties:
            tract_coordinates = t["geometry"]['coordinates']
            
            poly_type = t["geometry"]['type']

            area = get_analysis_area(t["properties"]["NAMELSADCO"], tract_coordinates, poly_type)
            
            
            response = requests.post(BAGP_URL, json=area)
            response = response.json()
            
            #print(response)
            properties = response["features"][0]["properties"]
            
            for p in unwanted_properties:
                properties.pop(p)

            #print(properties)
            temp = pd.DataFrame.from_dict([properties])
            temp["census_tract"] = t["properties"]["GEOID"]            
            #print(temp)
            
            df = pd.concat([df,temp])

    #print(df)  
    return df
            

In [ ]:
f = open("tract.json", encoding = "ISO-8859-1")
data = json.load(f)
data

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'bbox': [-118.263307, 33.782888, -118.253038, 33.791596],
    'type': 'Polygon',
    'coordinates': [[[-118.263307, 33.791148],
      [-118.25521000000002, 33.791596],
      [-118.25394199999998, 33.791414],
      [-118.253038, 33.791248],
      [-118.25314900000001, 33.789274],
      [-118.253713, 33.7872],
      [-118.253525, 33.784408],
      [-118.25356299999999, 33.783209],
      [-118.258121, 33.782925],
      [-118.25957399999999, 33.783055],
      [-118.26265600000002, 33.782888],
      [-118.26295700000001, 33.786701],
      [-118.263307, 33.791148]]]},
   'properties': {'STATEFP': '06',
    'COUNTYFP': '037',
    'TRACTCE': '294610',
    'AFFGEOID': '1400000US06037294610',
    'GEOID': '06037294610',
    'NAME': '2946.10',
    'NAMELSAD': 'Census Tract 2946.10',
    'STUSPS': 'CA',
    'NAMELSADCO': 'Los Angeles County',
    'STATE_NAME': 'California',
    'LSAD': 'CT',
    'ALAND': 823808,
    'A

In [ ]:
'''
properties = {'coastalhabitatvulnerable_unit': 'acres', 'linkage_diffuse_percent': 0, 'carbon_urbanforest_value': 129937, 'linkage_channelized_value': 0, 'floodplain500_natural_warning': '', 'grazing_percent': 0, 'lc_coniferhardwoodmix_value': 226, 'statefarm_percent': 0, 'pollutioncancer_warning': '', 'transitpriorityareas': 0, 'tsunami_value': 0, 'impair303stream_value': True, 'stormwaterretentionpools_units': 'pools', 'naturalseminaturallands_unit': 'acres', 'linkage_large_value': 0, 'baylands_unit': 'acres', 'wetlands_protected_value': 0, 'liquefaction_value': 55, 'naturalseminaturallands_warning': '', 'cropdollars_warning': '', 'naturalbaylands_value': 0, 'fishbarrier_unit': 'count', 'clnpriority_value': 0, 'lc_conifer_protected_unit': 'acres', 'prinathab_marginal_warning': '', 'floodplain100_value': 36, 'trailmilesexist_unit': 'miles', 'seismichazard_warning': '', 'watersites_planned_unit': 'count', 'groundwaterdependentecosystems_percent': 3, 'prinathab_ok_unit': 'percent', 'lc_shrub_protected_unit': 'acres', 'floodplain500_dac_unit': 'acres', 'pollutionexposure_warning': '', 'protected_easement_percent': 0, 'slr2100_warning': '', 'wildlifepinch_value': False, 'lc_herbaceous_unit': 'acres', 'floodplain500_dac_percent': 0, 'parkneed_dac_unit': 'acres', 'protected_easement_value': 0, 'drinkingwater_warning': '', 'airpollutionpm2_value': 656229, 'waterqualityindex_warning': '', 'recharge_value': 918, 'clnpriority_protected_unit': 'acres', 'naturalbaylands_unit': 'acres', 'carbon_soil_warning': '', 'vernalpools_protected_unit': 'acres', 'naturalbaylands_warning': '', 'prioritylandscapestreeplanting_dac_value': 0, 'stormwatervalue_value': 5651132, 'primefarm_warning': '', 'irrcapclass_warning': '', 'avoidedpollutant_warning': '', 'prinathab_firesev_warning': '', 'lc_coniferhardwoodmix_percent': 11, 'lc_herbaceous_percent': 2, 'airpollutionno2_dac_value': 0, 'lc_herbaceous_value': 36, 'cropdollars_value': 139342, 'wetlands_percent': 0, 'historicalfire_warning': '', 'firehazard_percent': 10, 'clnpriority_warning': '', 'conservation_plan_density_value': 0.270000010728836, 'impair303stream_warning': '', 'hirechargevulnerable_warning': '', 'floodplain500_natural_percent': 1, 'prioritylandscapestreeplanting_value': 6, 'coastalhab_migrationspace_warning': '', 'cropdollars_unit': 'dollars', 'mitigation_hotspots_value': 0, 'naturalriver_dac_value': 0, 'drinkingwater_unit': 'acres', 'rarespecies_warning': '', 'disadvcommunity_value': 0, 'lc_hardwood_protected_percent': 0, 'uniquefarm_value': 35, 'linkage_reglink_value': 0, 'vernalpools_protected_value': 0, 'carbon_urbanforest_unit': 'metric tons of CO2 equivalent', 'vernalpools_warning': '', 'linkage_diffuse_protected_percent': 0, 'keyriparian_protected_value': 0, 'lc_herbaceous_protected_percent': 0, 'prioritylandscapestreeplanting_warning': '', 'parkneed_dac_value': 0, 'disadvcommunity_percent': 0, 'coastalhabitatvulnerable_value': 0, 'linkage_reglink_unit': 'acres', 'uniquefarm_percent': 2, 'waterbasin_warning': '', 'lc_hardwood_value': 0, 'recharge_unit': 'acre-feet per year', 'impair303waterbody_unit': 'boolean', 'displacement_typos_unit': 'acres', 'arearesilience_warning': '', 'parkneed_warning': '', 'slr2050_dac_value': 0, 'hirechargevulnerable_dac_percent': 0, 'urbheatisland_air_value': 545, 'pubrecland_value': 17, 'prinathab_ok_percent': 0, 'naturalriver_value': 0, 'seismichazard_unit': 'acres', 'watersites_existing_unit': 'count', 'airpollutionno2_warning': '', 'acres': 2081, 'airpollutionno2_dac_unit': 'grams per year', 'localfarm_unit': 'acres', 'naturalriver_percent': 0, 'lc_herbaceous_protected_value': 0, 'irrcapclass_value': 0, 'protected_all_value': 17, 'naturalseminaturallands_percent': 0, 'linkage_diffuse_protected_value': 0, 'tsunami_unit': 'acres', 'primefarm_value': 0, 'runoff_unit': 'acre-feet per year', 'waterbasin_unit': 'boolean', 'waterqualityindex_value': 'higher than average', 'morewater_warmwet_value': 7, 'lc_conifer_protected_value': 0, 'floodplain100_unit': 'acres', 'displacement_typos_value': 0, 'watersites_existing_value': 0, 'historicalfire_percent': 0, 'protected_all_unit': 'acres', 'storieindex_unit': 'acres', 'protected_fee_warning': '', 'avoidedpollutant_value': 7141, 'airpollutionno2_value': 3752284, 'naturalriver_dac_unit': 'acres', 'slr2100_percent': 0, 'airpollutionno2_dac_percent': 0, 'liquefaction_warning': '', 'developmentprojects': [], 'tsunami_warning': '', 'linkage_intensified_percent': 0, 'baylands_warning': '', 'rainlandslides_percent': 0, 'urbanrecharge_value': 2056, 'parkneed_value': 15, 'wildlifepinch_warning': '', 'slr2100_value': 0, 'linkage_diffuse_unit': 'acres', 'bikeroutes1_2_warning': '', 'seismichazard_percent': 100, 'lc_hardwood_protected_unit': 'acres', 'climate_migration_unit': 'acres', 'stormwatervalue_warning': '', 'climate_migration_value': 0, 'floodplain500_warning': '', 'hirechargevulnerable_dac_unit': 'acres', 'liquefaction_percent': 3, 'clnpriority_percent': 0, 'arearesilience_value': 'lower than average', 'arearesilience_unit': 'score', 'impair303waterbody_warning': '', 'mitigation_hotspots_warning': '', 'waterbasin_value': False, 'linkage_reglink_warning': '', 'pubrecland_unit': 'acres', 'trailmilespotential_value': 0, 'linkage_reglink_protected_percent': 0, 'stormwaterretention_value': 280321, 'coastalhab_migrationspace_percent': 0, 'pollutioncancer_value': 0, 'lc_conifer_unit': 'acres', 'bikeroutes1_2_value': 2, 'drinkingwater_percent': 0, 'avoidedpollutant_unit': 'kg/yr', 'floodplain500_natural_unit': 'acres', 'rainlandslides_warning': '', 'linkage_large_percent': 0, 'tevertebrates_unit': 'percentile', 'wetlands_protected_percent': 0, 'pollutionexposure_unit': 'acres', 'statefarm_unit': 'acres', 'grazing_warning': '', 'pollutioncancer_unit': 'acres', 'clnpriority_unit': 'acres', 'communityconcern_unit': 'acres', 'slr2100_unit': 'acres', 'trailmilesexist_warning': '', 'groundwaterdependentecosystems_value': 55, 'linkage_reglink_protected_unit': 'acres', 'drinkingwater_value': 0, 'prioritylandscapestreeplanting_unit': 'acres', 'stormwatervalue_unit': 'dollars', 'title': 'Alameda County', 'linkage_diffuse_value': 0, 'slr2050_percent': 0, 'lc_hardwood_percent': 0, 'prioritylandscapestreeplanting_dac_percent': 0, 'urbanrecharge_text': 'has medium potential', 'bikeroutes1_unit': 'miles', 'reservoir_unit': 'boolean', 'wetlands_protected_unit': 'acres', 'linkage_large_unit': 'acres', 'statefarm_value': 0, 'lc_conifer_value': 0, 'groundwaterdependentecosystems_unit': 'acres', 'runoff_value': 777, 'mitigation_hotspots_unit': 'score', 'trailmilesexist_value': 2, 'carbon_aboveground_value': 853, 'linkage_intensified_unit': 'acres', 'storieindex_warning': '', 'clnpriority_protected_value': 0, 'protected_fee_unit': 'acres', 'tevertebrates_value': '40th - 60th', 'baylands_percent': 0, 'prinathab_firesev_value': 0, 'lc_hardwood_protected_value': 0, 'runoff_warning': '', 'wu_interface_warning': '', 'protected_fee_percent': 1, 'floodplain500_percent': 100, 'lc_shrub_protected_percent': 0, 'fishbarrier_value': 0, 'carbon_soil_unit': 'metric tons of CO2 equivalent', 'prioritylandscapestreeplanting_percent': 0, 'prinathab_marginal_percent': 0, 'naturalbaylands_percent': 0, 'parkneed_unit': 'acres', 'reservoir_warning': '', 'storieindex_value': 0, 'impair303stream_unit': 'boolean', 'bikeroutes1_warning': '', 'lc_coniferhardwoodmix_protected_unit': 'acres', 'firehazard_warning': '', 'carbon_addldidyouknow_unit': 'metric tons of CO2 equivalent', 'airpollutionpm2_unit': 'grams per year', 'urbheatisland_air_unit': 'acres', 'keyriparian_protected_percent': 0, 'lc_hardwood_unit': 'acres', 'communityconcern_value': 0, 'linkage_intensified_value': 0, 'baylands_value': 0, 'floodplain100_percent': 2, 'hirechargevulnerable_percent': 63, 'historicalfire_unit': 'acres', 'lc_shrub_protected_value': 0, 'rarespecies_unit': 'boolean', 'linkage_channelized_percent': 0, 'watersites_existing_warning': '', 'trailmilespotential_warning': '', 'protected_fee_value': 17, 'bikeroutes1_2_unit': 'miles', 'historicalfire_value': 0, 'prioritylandscapestreeplanting_dac_unit': 'acres', 'stormwaterretentionpools_value': 112, 'carbon_soil_value': 46610, 'rainlandslides_unit': 'acres', 'slr2050_unit': 'acres', 'allfarming_percent': 2, 'liquefaction_unit': 'acres', 'naturalriver_warning': '', 'protected_easement_unit': 'acres', 'morewater_hotdry_value': 21, 'floodplain500_value': 2081, 'wetlands_unit': 'acres', 'prinathab_marginal_unit': 'percent', 'pollutioncancer_percent': 0, 'keyriparian_protected_unit': 'miles', 'conservation_plan_density_text': 'some', 'prinathab_warning': '', 'reservoir_value': False, 'communityconcern_percent': 0, 'morewater_warmwet_warning': '', 'uniquefarm_warning': '', 'lc_herbaceous_protected_unit': 'acres', 'linkage_intensified_warning': '', 'floodplain100_warning': '', 'prinathab_marginal_value': 0, 'linkage_reglink_protected_value': 0, 'localfarm_percent': 0, 'morewater_warmwet_unit': 'acre-feet per year', 'statefarm_warning': '', 'naturalriver_dac_percent': 0, 'naturalriver_unit': 'acres', 'stormwaterretention_unit': 'cubic meters', 'hirechargevulnerable_value': 1313, 'localfarm_warning': '', 'urbanrecharge_unit': 'acres', 'lc_coniferhardwoodmix_protected_value': 0, 'linkage_diffuse_protected_unit': 'acres', 'irrcapclass_unit': 'acres', 'slr2050_value': 0, 'primefarm_unit': 'acres', 'airpollutionpm2_warning': '', 'bikeroutes1_value': 0, 'agriculturepolicies': [], 'fishbarrier_warning': '', 'stormwaterretention_warning': '', 'naturalseminaturallands_value': 0, 'prinathab_ok_value': 0, 'communityconcern_warning': '', 'linkage_large_warning': '', 'slr2050_dac_percent': 0, 'hirechargevulnerable_unit': 'acres', 'protected_easement_warning': '', 'pollutionexposure_percent': 0, 'popularity_value': 5, 'irrcapclass_percent': 0, 'wetlands_value': 0, 'primefarm_percent': 0, 'linkage_reglink_percent': 0, 'parkneed_percent': 1, 'prinathab_firesev_percent': 0, 'prinathab_value': 0}
#properties = {"number 1" : 1, "number 2" : 3}
temp = pd.DataFrame.from_dict([properties])
temp'''

'\nproperties = {\'coastalhabitatvulnerable_unit\': \'acres\', \'linkage_diffuse_percent\': 0, \'carbon_urbanforest_value\': 129937, \'linkage_channelized_value\': 0, \'floodplain500_natural_warning\': \'\', \'grazing_percent\': 0, \'lc_coniferhardwoodmix_value\': 226, \'statefarm_percent\': 0, \'pollutioncancer_warning\': \'\', \'transitpriorityareas\': 0, \'tsunami_value\': 0, \'impair303stream_value\': True, \'stormwaterretentionpools_units\': \'pools\', \'naturalseminaturallands_unit\': \'acres\', \'linkage_large_value\': 0, \'baylands_unit\': \'acres\', \'wetlands_protected_value\': 0, \'liquefaction_value\': 55, \'naturalseminaturallands_warning\': \'\', \'cropdollars_warning\': \'\', \'naturalbaylands_value\': 0, \'fishbarrier_unit\': \'count\', \'clnpriority_value\': 0, \'lc_conifer_protected_unit\': \'acres\', \'prinathab_marginal_warning\': \'\', \'floodplain100_value\': 36, \'trailmilesexist_unit\': \'miles\', \'seismichazard_warning\': \'\', \'watersites_planned_unit\': \'c

# Getting Individual County Data

Alameda, Marin, San Mateo, Napa, Contra Costa, Santa Clara, Sonoma, San Francisco, Solano

In [ ]:
alameda_str = ["Alameda County"]
alameda_tract = get_all_tracts(alameda_str)
alameda_tract[alameda_tract["acres",census_tract]]

KeyboardInterrupt: 

In [ ]:
alameda_tract = pd.read_csv('alameda_tract.csv')
alameda_tract["acres"]

0       499
1      1125
2       213
3       118
4       113
       ... 
373     621
374     383
375     143
376     270
377     227
Name: acres, Length: 378, dtype: int64

In [ ]:
marin_str = ['Marin County']
marin_tract = get_all_tracts(marin_str)

   coastalhabitatvulnerable_unit  linkage_diffuse_percent  \
0                          acres                        0   
0                          acres                        0   
0                          acres                        7   
0                          acres                       42   
0                          acres                        0   
..                           ...                      ...   
0                          acres                        2   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   
0                          acres                       38   

    carbon_urbanforest_value  linkage_channelized_value  \
0                     108203                          0   
0                      16671                          0   
0                      42991                          0   
0                         49   

In [ ]:
marin_tract

In [ ]:
san_mateo_str = ['San Mateo County']
san_mateo_tract = get_all_tracts(san_mateo_str)

   coastalhabitatvulnerable_unit  linkage_diffuse_percent  \
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   
..                           ...                      ...   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   

    carbon_urbanforest_value  linkage_channelized_value  \
0                       2963                          0   
0                       2794                          0   
0                        706                          0   
0                       3470   

In [ ]:
san_mateo_tract

In [ ]:
san_mateo_tract

In [ ]:
napa_str = ['Napa County']
napa_tract = get_all_tracts(napa_str)

  coastalhabitatvulnerable_unit  linkage_diffuse_percent  \
0                         acres                        0   
0                         acres                        0   
0                         acres                        0   
0                         acres                        0   
0                         acres                       17   
0                         acres                        0   
0                         acres                        0   
0                         acres                       33   
0                         acres                        0   
0                         acres                        0   
0                         acres                        0   
0                         acres                       28   
0                         acres                        0   
0                         acres                        0   
0                         acres                        0   
0                         acres         

In [ ]:
napa_tract

In [ ]:
contra_str = ['Contra Costa County']
contra_tract = get_all_tracts(contra_str)

   coastalhabitatvulnerable_unit  linkage_diffuse_percent  \
0                          acres                       99   
0                          acres                        0   
0                          acres                        0   
0                          acres                       25   
0                          acres                       58   
..                           ...                      ...   
0                          acres                       11   
0                          acres                        2   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   

    carbon_urbanforest_value  linkage_channelized_value  \
0                       2524                          0   
0                       5231                          0   
0                      10616                          0   
0                       4201   

In [ ]:
contra_tract

In [ ]:
santa_clara_str = ['Santa Clara County']
santa_clara_tract = get_all_tracts(santa_clara_str)

In [ ]:
santa_clara_tract

In [ ]:
sonoma_str = ['Sonoma County']
sonoma_tract = get_all_tracts(sonoma_str)

In [ ]:
sonoma_tract

In [ ]:
def get_sf_tract(counties):
    df = pd.DataFrame()
    BAGP_URL = "https://www.bayareagreenprint.org/api/"
    unwanted_properties = ["waterpolicies", "habitatpolicies", "intersections","conservationpolicies"]
    f = open("tract.json", encoding = "ISO-8859-1")
    data = json.load(f)

    for t in data["features"]: #i in range (500):
        #t = data["features"][i]
        if t["properties"]["NAMELSADCO"] in counties:
            tract_coordinates = t["geometry"]['coordinates']
            
            poly_type = t["geometry"]['type']

            area = get_analysis_area(t["properties"]["NAMELSADCO"], tract_coordinates, poly_type)
            
            
            response = requests.post(BAGP_URL, json=area)
            response = response.json()

            try:
                properties = response["features"][0]["properties"]
                
                for p in unwanted_properties:
                    properties.pop(p)

                #print(properties)
                temp = pd.DataFrame.from_dict([properties])
                temp["census_tract"] = t["properties"]["GEOID"]            
                #print(temp)
                
                df = pd.concat([df,temp])
            except:
                print(response)
                print(area)
            

    #print(df)  
    return df
            
# clipping data to get around the 4 acres
get_sf_tract(san_francisco_str)

{'error': 'The selected area is 4 acres in size, which is smaller than the minimum of 5 acres. Please pick a larger area.'}
{'name': 'San Francisco County', 'type': 'FeatureCollection', 'crs': {'properties': {'name': 'urn:ogc:def:crs:OGC:1.3:CRS84'}, 'type': 'name'}, 'features': [{'type': 'Feature', 'geometry': {'coordinates': [[[-122.41386600000001, 37.781863], [-122.411985, 37.780952], [-122.41254799999999, 37.780508], [-122.41336499999998, 37.77986200000001], [-122.41386600000001, 37.781863]]], 'type': 'Polygon'}, 'properties': {'name': 'San Francisco County'}}]}


coastalhabitatvulnerable_unit  linkage_diffuse_percent  \
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   
..                           ...                      ...   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   

    carbon_urbanforest_value  linkage_channelized_value  \
0                       3768                          0   
0                        149                          0   
0                        211                          0   
0                        848                          0   
0                       3710                          0   
..                       ...                        ...   
0                       4127                          0   
0                       1932                          0   
0                        718                          0   
0                      11828                          0   
0                          0                          0   

   floodplain500_natural_warning  grazing_percent  \
0        Below Acreage Threshold                0   
0                                               0   
0                                               0   
0        Below Acreage Threshold                0   
0        Below Acreage Threshold                0   
..                           ...              ...   
0                                               0   
0        Below Acreage Threshold                0   
0        Below Acreage Threshold                0   
0                                               0   
0                                               0   

    lc_coniferhardwoodmix_value  statefarm_percent pollutioncancer_warning  \
0                             0                  0                           
0                             0                  0                           
0                             0                  0                           
0                             0                  0                           
0                             0                  0                           
..                          ...                ...                     ...   
0                             0                  0                           
0                             0                  0                           
0                             0                  0                           
0                             8                  0                           
0                             0                  0                           

    transitpriorityareas  ...  disadvcommunity_warning  slr2050_warning  \
0                      1  ...                                             
0                      1  ...                                             
0                      1  ...                                             
0                      1  ...                                             
0                      1  ...                                             
..                   ...  ...                      ...              ...   
0                      1  ...                                             
0                      1  ...                                             
0                      1  ...                                             
0                      1  ...                                             
0                      0  ...                                             

   displacement_typos_percent pubrecland_percent  grazing_value  \
0                  

In [ ]:
san_francisco_str = ['San Francisco County']
san_francisco_tract = get_sf_tract(san_francisco_str)

KeyboardInterrupt: 

In [ ]:
san_francisco_tract

coastalhabitatvulnerable_unit  linkage_diffuse_percent  \
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   
..                           ...                      ...   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   
0                          acres                        0   

    carbon_urbanforest_value  linkage_channelized_value  \
0                       3768                          0   
0                        149                          0   
0                        211                          0   
0                        848                          0   
0                       3710                          0   
..                       ...                        ...   
0                       4127                          0   
0                       1932                          0   
0                        718                          0   
0                      11828                          0   
0                          0                          0   

   floodplain500_natural_warning  grazing_percent  \
0        Below Acreage Threshold                0   
0                                               0   
0                                               0   
0        Below Acreage Threshold                0   
0        Below Acreage Threshold                0   
..                           ...              ...   
0                                               0   
0        Below Acreage Threshold                0   
0        Below Acreage Threshold                0   
0                                               0   
0                                               0   

    lc_coniferhardwoodmix_value  statefarm_percent pollutioncancer_warning  \
0                             0                  0                           
0                             0                  0                           
0                             0                  0                           
0                             0                  0                           
0                             0                  0                           
..                          ...                ...                     ...   
0                             0                  0                           
0                             0                  0                           
0                             0                  0                           
0                             8                  0                           
0                             0                  0                           

    transitpriorityareas  ...  disadvcommunity_warning  slr2050_warning  \
0                      1  ...                                             
0                      1  ...                                             
0                      1  ...                                             
0                      1  ...                                             
0                      1  ...                                             
..                   ...  ...                      ...              ...   
0                      1  ...                                             
0                      1  ...                                             
0                      1  ...                                             
0                      1  ...                                             
0                      0  ...                                             

   displacement_typos_percent pubrecland_percent  grazing_value  \
0                  

In [ ]:
solano_str = ['Solano County']
solano_tract = get_all_tracts(solano_str)

In [ ]:
solano_tract

In [ ]:
bay_area_tracts = pd.concat([alameda_tract, marin_tract, san_mateo_tract, napa_tract, 
    contra_tract, santa_clara_tract, sonoma_tract, solano_tract])
bay_area_tracts

In [ ]:
# note this includes all but San Francisco

bay_area_tracts_except_sf = pd.read_csv('most_bay_area_tracts.csv')
bay_area_tracts_except_sf

coastalhabitatvulnerable_unit  linkage_diffuse_percent  \
0                            acres                        0   
1                            acres                        0   
2                            acres                        0   
3                            acres                        0   
4                            acres                        0   
...                            ...                      ...   
1518                         acres                        0   
1519                         acres                       19   
1520                         acres                        0   
1521                         acres                        0   
1522                         acres                        0   

      carbon_urbanforest_value  linkage_channelized_value  \
0                        11922                          0   
1                        12630                          0   
2                         2085                          0   
3                         2643                          0   
4                         2686                          0   
...                        ...                        ...   
1518                      7407                          0   
1519                     11618                       2306   
1520                     14145                          0   
1521                      3804                          0   
1522                      9173                          0   

     floodplain500_natural_warning  grazing_percent  \
0                              NaN                0   
1                              NaN                0   
2                              NaN                0   
3                              NaN                0   
4                              NaN                0   
...                            ...              ...   
1518                           NaN                0   
1519                           NaN               66   
1520                           NaN                0   
1521                           NaN                0   
1522                           NaN                0   

      lc_coniferhardwoodmix_value  statefarm_percent  pollutioncancer_warning  \
0                               0                  0                      NaN   
1                               0                  0                      NaN   
2                               0                  0                      NaN   
3                               0                  0                      NaN   
4                               0                  0                      NaN   
...                           ...                ...                      ...   
1518                            0                  0                      NaN   
1519                          184                  1                      NaN   
1520                            3                  0                      NaN   
1521                            0                  0                      NaN   
1522                            0                  0                      NaN   

      transitpriorityareas  ...  disadvcommunity_warning  slr2050_warning  \
0                        0  ...                      NaN              NaN   
1                        1  ...                      NaN              NaN   
2                        1  ...                      NaN              NaN   
3                        1  ...                      NaN              NaN   
4                        1  ...                      NaN              NaN   
...                    ...  ...                      ...              ...   
1518                     0  ...                      NaN              NaN   
1519                     0  ...                      NaN              NaN   
1520                     0  ...                      NaN              NaN   
1521                     0  ...                      NaN              NaN   
1522                     1  ...   

In [16]:
bay_area_tracts = pd.concat([bay_area_tracts_except_sf, san_francisco_tract])
bay_area_tracts

NameError: name 'bay_area_tracts_except_sf' is not defined

In [17]:
bay_area_tracts = pd.read_csv('bay_area_tracts.csv')
#bay_area_tracts[bay_area_tracts["Census_tract"]]
bay_area_tracts

coastalhabitatvulnerable_unit  linkage_diffuse_percent  \
0                            acres                        0   
1                            acres                        0   
2                            acres                        0   
3                            acres                        0   
4                            acres                        0   
...                            ...                      ...   
1759                         acres                        0   
1760                         acres                        0   
1761                         acres                        0   
1762                         acres                        0   
1763                         acres                        0   

      carbon_urbanforest_value  linkage_channelized_value  \
0                        11922                          0   
1                        12630                          0   
2                         2085                          0   
3                         2643                          0   
4                         2686                          0   
...                        ...                        ...   
1759                      4127                          0   
1760                      1932                          0   
1761                       718                          0   
1762                     11828                          0   
1763                         0                          0   

     floodplain500_natural_warning  grazing_percent  \
0                              NaN                0   
1                              NaN                0   
2                              NaN                0   
3                              NaN                0   
4                              NaN                0   
...                            ...              ...   
1759                           NaN                0   
1760       Below Acreage Threshold                0   
1761       Below Acreage Threshold                0   
1762                           NaN                0   
1763                           NaN                0   

      lc_coniferhardwoodmix_value  statefarm_percent  pollutioncancer_warning  \
0                               0                  0                      NaN   
1                               0                  0                      NaN   
2                               0                  0                      NaN   
3                               0                  0                      NaN   
4                               0                  0                      NaN   
...                           ...                ...                      ...   
1759                            0                  0                      NaN   
1760                            0                  0                      NaN   
1761                            0                  0                      NaN   
1762                            8                  0                      NaN   
1763                            0                  0                      NaN   

      transitpriorityareas  ...  disadvcommunity_warning  slr2050_warning  \
0                        0  ...                      NaN              NaN   
1                        1  ...                      NaN              NaN   
2                        1  ...                      NaN              NaN   
3                        1  ...                      NaN              NaN   
4                        1  ...                      NaN              NaN   
...                    ...  ...                      ...              ...   
1759                     1  ...                      NaN              NaN   
1760                     1  ...                      NaN              NaN   
1761                     1  ...                      NaN              NaN   
1762                     1  ...                      NaN              NaN   
1763                     0  ...   

In [ ]:
carrie = pd.read_csv('NBS_climateRisk_for_DSS_analysis.csv')
carrie = carrie.fillna(0)
useful_cols = list(carrie[carrie['Inclusion Priority'] > 0].sort_values('Inclusion Priority').iloc[:, 0])
useful_cols.insert(0,'census_tract')

list(carrie[carrie['Reason for inclusion'] == 'NBS'].iloc[:, 0])

['wetlands_value',
 'vernalpools_value',
 'naturalriver_value',
 'naturalbaylands_value',
 'hirechargevulnerable_value',
 'floodplain500_natural_value',
 'carbon_urbanforest_value',
 'drinkingwater_value',
 'reservoir_value',
 'waterbasin_value']

In [ ]:
bay_area_tracts_cleaned = bay_area_tracts[useful_cols]
bay_area_tracts_cleaned

census_tract  carbon_urbanforest_value  floodplain100_value  \
0       6001451704                     11922                    0   
1       6001428301                     12630                  151   
2       6001407000                      2085                    0   
3       6001422400                      2643                    0   
4       6001423200                      2686                    0   
...            ...                       ...                  ...   
1759    6075021500                      4127                    0   
1760    6075020701                      1932                    0   
1761    6075026404                       718                    0   
1762    6075030400                     11828                    0   
1763    6075980401                         0                    0   

      floodplain500_value  floodplain500_natural_value  \
0                       0                            0   
1                     231                           27   
2                       0                            0   
3                       0                            0   
4                       0                            0   
...                   ...                          ...   
1759                    0                            0   
1760                    0                            0   
1761                    0                            0   
1762                    0                            0   
1763                    0                            0   

     waterqualityindex_value  drinkingwater_value  reservoir_value  \
0         lower than average                    0            False   
1         lower than average                    0            False   
2         lower than average                    0            False   
3         lower than average                    0            False   
4         lower than average                    0            False   
...                      ...                  ...              ...   
1759      lower than average                    0            False   
1760      lower than average                    0            False   
1761      lower than average                    0            False   
1762      lower than average                    0            False   
1763      lower than average                    0            False   

      hirechargevulnerable_value  waterbasin_value  ...  \
0                            426             False  ...   
1                              0             False  ...   
2                              0             False  ...   
3                              0             False  ...   
4                              0             False  ...   
...                          ...               ...  ...   
1759                           0             False  ...   
1760                           0             False  ...   
1761                           0             False  ...   
1762                           0             False  ...   
1763                           0             False  ...   

      watersites_existing_value  protected_fee_value  linkage_diffuse_value  \
0                             0                   21                      0   
1                             0                   26                      0   
2                             0                    2                      0   
3                             0                    1                      0   
4                             0                    0                      0   
...                         ...                  ...                    ...   
1759                          0                    3                      0   
1760                          0                    2                      0   
1761                          0                    1                      0   
1762                          0                    5                      0   
1763                          0                    0         

In [27]:
bay_area_tracts = pd.read_csv('bay_area_tracts.csv')
acres_df = bay_area_tracts[["acres","census_tract"]]
master_data = pd.read_csv("master_data_old.csv")
#acres_df
master_data = pd.merge(master_data, acres_df, left_on='Census_Tract', right_on='census_tract')
master_data["acres"]
master_data

Census_Tract  OBJECTID           ID  REGION    ACSTOTPOP   ACSIPOVBAS  \
0       6001400100   11497.5  60014001001     9.0  1517.500000  1507.000000   
1       6001400200   11499.5  60014002001     9.0   991.500000   983.500000   
2       6001400300   11502.5  60014003002     9.0  1264.500000  1254.750000   
3       6001400400   11506.0  60014004002     9.0  1393.000000  1389.000000   
4       6001400500   11509.0  60014005002     9.0  1340.333333  1340.333333   
...            ...       ...          ...     ...          ...          ...   
1750    6097154100   35583.5  60971541002     9.0   921.500000   921.500000   
1751    6097154201   35587.5  60971542012     9.0   946.750000   940.250000   
1752    6097154202   35591.5  60971542022     9.0  1563.750000  1548.750000   
1753    6097154304   35595.5  60971543042     9.0   581.750000   564.000000   
1754    6097154306   35601.5  60971543061     9.0   781.000000   781.000000   

       ACSEDUCBAS    ACSTOTHH  ACSTOTHU  ACSUNEMPBAS  ...  \
0     1206.000000  637.000000    705.50   793.500000  ...   
1      802.500000  415.000000    428.00   617.000000  ...   
2     1006.000000  604.750000    668.50   818.250000  ...   
3     1052.333333  580.000000    628.00   867.333333  ...   
4     1006.000000  547.666667    589.00   885.333333  ...   
...           ...         ...       ...          ...  ...   
1750   754.250000  348.000000    445.75   538.750000  ...   
1751   672.250000  353.750000    360.25   461.500000  ...   
1752  1152.500000  630.000000    639.25   820.750000  ...   
1753   435.750000  249.000000    443.00   291.000000  ...   
1754   731.000000  438.500000    675.50   459.000000  ...   

      linkage_diffuse_value  linkage_intensified_value  \
0                         0                        135   
1                         0                          0   
2                         0                          0   
3                         0                          0   
4                         0                          0   
...                     ...                        ...   
1750                  40900                      28065   
1751                   1752                        655   
1752                  16351                      17266   
1753                  81066                     105815   
1754                   3354                        806   

      linkage_channelized_value  linkage_large_value  linkage_reglink_value  \
0                           529                  305                    515   
1                             0                    0                      0   
2                             0                    0                      0   
3                             0                    0                      0   
4                             0                    0                      0   
...                         ...                  ...                    ...   
1750                      30859                    0                  81194   
1751                         56                    0                   1685   
1752                       3606                33693                  10640   
1753                      20722                26840                  57564   
1754                        642                    0                    504   

      displacement_typos_value  communityconcern_value  disadvcommunity_value  \
0                            0                       0                      0   
1                            0                       0                      0   
2                            1                       1                      0   
3                          178                       0                      0   
4                          146                       1                      0   
...                        ...                     ...                    ...   
1750                         0                       0                      0   
1751                         0

In [28]:
master = pd.read_csv('master_data.csv')
#master["acres"]

## Getting GeoPandas coordinates

In [29]:
f = open("tract.json", encoding = "ISO-8859-1")
data = json.load(f)
data


{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'bbox': [-118.263307, 33.782888, -118.253038, 33.791596],
    'type': 'Polygon',
    'coordinates': [[[-118.263307, 33.791148],
      [-118.25521000000002, 33.791596],
      [-118.25394199999998, 33.791414],
      [-118.253038, 33.791248],
      [-118.25314900000001, 33.789274],
      [-118.253713, 33.7872],
      [-118.253525, 33.784408],
      [-118.25356299999999, 33.783209],
      [-118.258121, 33.782925],
      [-118.25957399999999, 33.783055],
      [-118.26265600000002, 33.782888],
      [-118.26295700000001, 33.786701],
      [-118.263307, 33.791148]]]},
   'properties': {'STATEFP': '06',
    'COUNTYFP': '037',
    'TRACTCE': '294610',
    'AFFGEOID': '1400000US06037294610',
    'GEOID': '06037294610',
    'NAME': '2946.10',
    'NAMELSAD': 'Census Tract 2946.10',
    'STUSPS': 'CA',
    'NAMELSADCO': 'Los Angeles County',
    'STATE_NAME': 'California',
    'LSAD': 'CT',
    'ALAND': 823808,
    'A

In [ ]:
def bike_fence_format(s):
    s = s.replace('[', '').replace(']', '').split(',')
    s = [float(x) for x in s]

    return s

df['FENCE_LOC'] = df['FENCE_LOC'].apply(bike_fence_format)


df['LAT'] = df['FENCE_LOC'].apply(lambda x: x[1::2])
df['LON'] = df['FENCE_LOC'].apply(lambda x: x[::2])

geom_list = [(x, y) for x, y  in zip(df['LON'],df['LAT'])]

geom_list_2 = [Polygon(tuple(zip(x, y))) for x, y in geom_list]

polygon_gdf =  gpd.GeoDataFrame(geometry=geom_list_2)






<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=08c08e4f-c970-41e1-98db-afa3328b10c6' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>